# ALBERT + CNN

In [1]:
# importing libraries
import warnings
warnings.filterwarnings("ignore")
import pandas as pd
import pickle
#from transformers import 
import numpy as np
from numpy import zeros, newaxis
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from gensim.models import Word2Vec
from gensim.models import KeyedVectors
from tqdm import tqdm
import random as rn
import tensorflow 

from wordcloud import WordCloud, STOPWORDS 

import nltk
from nltk.sentiment.vader import SentimentIntensityAnalyzer
#nltk.download('vader_lexicon')

import tensorflow as tf
from tensorflow.keras.layers import Conv1D,AveragePooling1D,MaxPooling1D
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense,Flatten,Embedding,Input,concatenate,Activation,Dropout,BatchNormalization,LSTM
from tensorflow.keras import regularizers,Model
from tensorflow.keras.regularizers import l1,l2
from tensorflow.keras.callbacks import TensorBoard, Callback, EarlyStopping, ModelCheckpoint,LearningRateScheduler
import tensorflow_hub as hub

from transformers import AlbertTokenizer

In [2]:
train = pd.read_csv("google-quest-challenge/train.csv")

In [3]:

def get_sentiments(df,column_list):
    '''
    sentiments from question_title
    '''
     
    for col in column_list:
        
        sid = SentimentIntensityAnalyzer()
        neg=[]
        neu=[]
        pos=[]
        comp=[]
    
        for txt in df[col]:
            ss = sid.polarity_scores(txt)
            neg.append(ss['neg'])
            neu.append(ss['neu'])
            pos.append(ss['pos'])
            comp.append(ss['compound'])

        df[col+"_neg"] = neg
        df[col+"_neu"] = neu
        df[col+"_pos"] = pos
        df[col+"_comp"] = comp
    
    return df

#==================================================

def countVectorizer(df_train,df_cv,column):
    '''
    function to vectorize categorical data
    '''
    # one-hot encoding 'category' feature
    vect = CountVectorizer(binary=True)
    vect.fit(df_train[column])
    encoded_train = vect.transform(df_train[column]).todense()
    encoded_cv = vect.transform(df_cv[column]).todense()
    
    return encoded_train, encoded_cv, vect

In [4]:
#=================================PREPROCESSING===================================
    
# preprocessing host name 
train['host'] = train['host'].apply(lambda x: x.split('.')[-2])
train['host'] = train['host'].apply(lambda x: x.lower())
train['host'] = train['host'].apply(lambda x: x.strip())
    
# preprocessing 'category' to lower-case and stripping leading and tailing spaces 
train['category'] = train['category'].apply(lambda x: x.lower())
train['category'] = train['category'].apply(lambda x: x.strip())
    
#=================================FEATURE ENGINEERING=============================
    
# taking length of question title, question body, answer
train['q_title_length'] = train['question_title'].apply(lambda x: len(x.split(' ')))
train['q_body_length'] = train['question_body'].apply(lambda x: len(x.split(' ')))
train['answer_length'] = train['answer'].apply(lambda x: len(x.split(' ')))
#train.head()
    
train = get_sentiments(train,['question_title','question_body','answer'])

In [5]:
# separation of features and class-labels
class_labels = ['question_asker_intent_understanding', 'question_body_critical', 'question_conversational', 
                    'question_expect_short_answer', 'question_fact_seeking', 'question_has_commonly_accepted_answer', 
                    'question_interestingness_others', 'question_interestingness_self', 'question_multi_intent', 
                    'question_not_really_a_question', 'question_opinion_seeking', 'question_type_choice', 
                    'question_type_compare', 'question_type_consequence', 'question_type_definition', 
                    'question_type_entity', 'question_type_instructions', 'question_type_procedure', 
                    'question_type_reason_explanation', 'question_type_spelling', 'question_well_written',
                    'answer_helpful', 'answer_level_of_information', 'answer_plausible', 'answer_relevance', 
                    'answer_satisfaction', 'answer_type_instructions', 'answer_type_procedure', 
                    'answer_type_reason_explanation', 'answer_well_written']

X = train.drop(columns=class_labels,axis=1)
y = train[class_labels]

print(X.shape, y.shape)

(6079, 26) (6079, 30)


In [6]:
# splitting data
x_train,x_cv,y_train,y_cv = train_test_split(X,y,test_size=0.15)
print("Train shape: ", x_train.shape,y_train.shape)
print("Test shape: ", x_cv.shape,y_cv.shape)

Train shape:  (5167, 26) (5167, 30)
Test shape:  (912, 26) (912, 30)


In [7]:
# Encoding categorical data
category_encoded_train, category_encoded_cv, category_vectorizer = countVectorizer(x_train,x_cv,'category')
host_encoded_train, host_encoded_cv, host_vectorizer = countVectorizer(x_train,x_cv,'host')

print(category_encoded_train.shape)
print(host_encoded_train.shape)

(5167, 5)
(5167, 6)


In [8]:
# ALBERT tokenizer (pretrained)
tokenizer = AlbertTokenizer.from_pretrained('albert-base-v2')

def encode_text(text,max_len):
    
    '''
    function to encode text for input to ALBERT
    '''
    
    encoded_dict = tokenizer.encode_plus(text, None, max_length=max_len, pad_to_max_length=True,
                                       add_special_tokens=True)
    return encoded_dict
    
#================================================================================

def get_encoded_bert_inputs(df,max_len):
    '''
    
    '''
    q_input_ids = []
    q_masks = []
    q_segments = []
    a_input_ids = []
    a_masks = []
    a_segments = []
    
    # question encoding
    for i in df.index:
        q_text = df['question_title'][i] + " [SEP] " + df['question_body'][i]
        q_encoded_dict = encode_text(q_text,max_len)
        q_input_ids.append(q_encoded_dict['input_ids'])
        q_masks.append(q_encoded_dict['attention_mask'])
        q_segments.append(q_encoded_dict['token_type_ids'])
    
    # answer encoding
    for i in df.index:
        a_text = df['answer'][i]
        a_encoded_dict = encode_text(a_text,max_len)
        a_input_ids.append(a_encoded_dict['input_ids'])
        a_masks.append(a_encoded_dict['attention_mask'])
        a_segments.append(a_encoded_dict['token_type_ids'])
    
    return q_input_ids, q_masks, q_segments, a_input_ids, a_masks, a_segments


In [9]:
# getting inputs for ALBERT
q_input_ids,q_mask,q_seg,a_input_ids,a_mask,a_seg = get_encoded_bert_inputs(x_train,max_len=512)
q_input_ids_cv,q_mask_cv,q_seg_cv,a_input_ids_cv,a_mask_cv,a_seg_cv = get_encoded_bert_inputs(x_cv,max_len=512)

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (

...

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (

Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Truncation was not explicitely activated but `max_length` is provided a specific value, please use `truncation=True` to explicitely truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (

In [10]:
# defining base ALBERT layer
albert_layer = hub.KerasLayer("https://tfhub.dev/tensorflow/albert_en_base/1",
                              trainable=True)

INFO:absl:Using C:\Users\JAYANY\AppData\Local\Temp\tfhub_modules to cache modules.


In [14]:
from tqdm import tqdm

def get_text_vector(albert_layer,input_ids,mask,seg):
    '''
    function to get BERT output that represents whole input sequence
    '''
    
    for i in tqdm(range(len(input_ids))):
        enc, _ = albert_layer([input_ids[i:i+1],mask[i:i+1],seg[i:i+1]])
        
        if i>0:
            
            final_text_vec = tf.keras.layers.concatenate([final_text_vec,enc],axis=0)
        
        else:
            final_text_vec = enc
            
    return final_text_vec

In [15]:
# getting vector output (representing whole inpur sequence) of question from ALBERT for train data
question_vect = get_text_vector(albert_layer,q_input_ids,q_mask,q_seg)

100%|██████████████████████████████████████████████████████████████████████████████| 5167/5167 [12:39<00:00,  6.49it/s]


In [18]:
# getting vector output (representing whole inpur sequence) of answer from ALBERT for train data
answer_vect = get_text_vector(albert_layer,a_input_ids,a_mask,a_seg)

100%|██████████████████████████████████████████████████████████████████████████████| 5167/5167 [14:44<00:00,  5.75it/s]


In [21]:
# getting vector output (representing whole inpur sequence) of answer from ALBERT for cross-validation data
question_vect_cv = get_text_vector(albert_layer,q_input_ids_cv,q_mask_cv,q_seg_cv)

100%|████████████████████████████████████████████████████████████████████████████████| 912/912 [02:23<00:00,  6.03it/s]


In [24]:
# getting vector output (representing whole inpur sequence) of answer from ALBERT for cross-validation data
answer_vect_cv = get_text_vector(albert_layer,a_input_ids_cv,a_mask_cv,a_seg_cv)

100%|████████████████████████████████████████████████████████████████████████████████| 912/912 [02:03<00:00,  6.40it/s]


In [27]:
# concatenating question and answer output from ALBERT
final_text_vector_train = tf.keras.layers.concatenate([question_vect,answer_vect])
final_text_vector_cv = tf.keras.layers.concatenate([question_vect_cv,answer_vect_cv])

print("Train text vectorshape = ",final_text_vector_train.shape)
print("CV text vector shape = ",final_text_vector_cv.shape)

Train text vectorshape =  (5167, 1536)
CV text vector shape =  (912, 1536)


In [28]:
# concatenating and reshaping categorical and numerical data for train and cross-validation

train_vect_cat_num = np.hstack([category_encoded_train,host_encoded_train,
                                    x_train[['q_title_length','q_body_length','answer_length', 'question_title_neg',
                                             'question_title_neu', 'question_title_pos', 'question_title_comp', 
                                             'question_body_neg','question_body_neu', 'question_body_pos', 'question_body_comp', 
                                             'answer_neg','answer_neu', 'answer_pos', 'answer_comp']]])

cv_vect_cat_num = np.hstack([category_encoded_cv,host_encoded_cv,
                                 x_cv[['q_title_length','q_body_length','answer_length', 'question_title_neg',
                                       'question_title_neu', 'question_title_pos', 'question_title_comp', 
                                       'question_body_neg','question_body_neu', 'question_body_pos', 'question_body_comp', 
                                       'answer_neg','answer_neu', 'answer_pos', 'answer_comp']]])
train_vect_cat_num = train_vect_cat_num[:,:,newaxis]
cv_vect_cat_num = cv_vect_cat_num[:,:,newaxis]
print(train_vect_cat_num.shape, cv_vect_cat_num.shape)

(5167, 26, 1) (912, 26, 1)


## Model - CNN-1

This model does not perform convolution on ALBERT text vector output.

In [92]:
#fixing numpy RS
np.random.seed(42)

#fixing tensorflow RS
tensorflow.random.set_seed(32)
    
#python RS
rn.seed(12)

input1 = Input(shape=(1536,1), name = 'input_1')

flat_text = Flatten()(input1)
out_1 =  Dense(384,activation='sigmoid')(flat_text)
#====================================================================================================================


input2 = Input(shape=(26,1), name = 'input_2')
conv = Conv1D(filters = 8, kernel_size = 3,strides = 1, activation='relu',
                  kernel_initializer=tensorflow.keras.initializers.he_normal(seed=43),
                  kernel_regularizer=tensorflow.keras.regularizers.l2(0.1),
                  input_shape=(None,26,1))(input2)

flat_rem = Flatten()(conv)
out_2 =  Dense(48,activation='sigmoid')(flat_rem)
#====================================================================================================================

final_data = concatenate([out_1,out_2])

output = Dense(30,activation='sigmoid')(final_data)

# create model with 2 inputs
model = Model([input1,input2], output)

model.compile(loss=tensorflow.keras.losses.binary_crossentropy,
              optimizer=tensorflow.keras.optimizers.Adam(0.002),
              metrics=['mae'])
model.summary()

Model: "functional_27"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            [(None, 26, 1)]      0                                            
__________________________________________________________________________________________________
input_1 (InputLayer)            [(None, 1536, 1)]    0                                            
__________________________________________________________________________________________________
conv1d_32 (Conv1D)              (None, 24, 8)        32          input_2[0][0]                    
__________________________________________________________________________________________________
flatten_27 (Flatten)            (None, 1536)         0           input_1[0][0]                    
______________________________________________________________________________________

In [93]:

history_model = model.fit([final_text_vector_train,train_vect_cat_num], 
                          y_train, 
                                 epochs=50,
                                 verbose=2,batch_size=64,
                                 callbacks = [checkpoint],
                                 validation_split = 0.05)

Epoch 1/50
77/77 - 0s - loss: 1.8162 - mae: 0.1713 - val_loss: 1.6009 - val_mae: 0.1633
Epoch 2/50
77/77 - 0s - loss: 1.4411 - mae: 0.1597 - val_loss: 1.2886 - val_mae: 0.1589
Epoch 3/50
77/77 - 0s - loss: 1.1713 - mae: 0.1567 - val_loss: 1.0582 - val_mae: 0.1584
Epoch 4/50
77/77 - 0s - loss: 0.9688 - mae: 0.1550 - val_loss: 0.8873 - val_mae: 0.1594
Epoch 5/50
77/77 - 0s - loss: 0.8187 - mae: 0.1541 - val_loss: 0.7542 - val_mae: 0.1534
Epoch 6/50
77/77 - 0s - loss: 0.7050 - mae: 0.1528 - val_loss: 0.6573 - val_mae: 0.1522
Epoch 7/50
77/77 - 0s - loss: 0.6219 - mae: 0.1518 - val_loss: 0.5848 - val_mae: 0.1533
Epoch 8/50
77/77 - 0s - loss: 0.5591 - mae: 0.1508 - val_loss: 0.5326 - val_mae: 0.1512
Epoch 9/50
77/77 - 0s - loss: 0.5139 - mae: 0.1503 - val_loss: 0.4927 - val_mae: 0.1515
Epoch 10/50
77/77 - 0s - loss: 0.4794 - mae: 0.1491 - val_loss: 0.4665 - val_mae: 0.1547
Epoch 11/50
77/77 - 0s - loss: 0.4551 - mae: 0.1492 - val_loss: 0.4429 - val_mae: 0.1481
Epoch 12/50
77/77 - 0s - loss:

In [94]:
# spearman's correlation on train data

y_tr_pred = model.predict([final_text_vector_train,train_vect_cat_num])
spearman(y_tr_pred,y_train)


0.3246815850076294

In [95]:
# spearman's correlation on CV data
y_cv_pred = model.predict([final_text_vector_cv, cv_vect_cat_num])
spearman(y_cv_pred,y_cv)

0.27174858109247074

## Model - CNN-2

This model does not perform Convolution on any data (text and categorical+numerical)

In [112]:
 #fixing numpy RS
np.random.seed(42)

#fixing tensorflow RS
tensorflow.random.set_seed(32)

#python RS
rn.seed(12)

#input1
input1 = Input(shape=(1536,1), name = 'input_1')
flat_text = Flatten()(input1)
out_1 =  Dense(384,activation='sigmoid')(flat_text)
#====================================================================================================================

#input 2
input2 = Input(shape=(26,1), name = 'input_2')

flat_rem = Flatten()(input2)
out_2 =  Dense(24,activation='sigmoid')(flat_rem)
#====================================================================================================================

final_data = concatenate([out_1,out_2])

output = Dense(30,activation='sigmoid')(final_data)

# create model with 2 inputs
model = Model([input1,input2], output)

model.compile(loss=tensorflow.keras.losses.binary_crossentropy,
              optimizer=tensorflow.keras.optimizers.Adam(0.002),
              metrics=['mae'])
model.summary()

Model: "functional_37"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, 1536, 1)]    0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            [(None, 26, 1)]      0                                            
__________________________________________________________________________________________________
flatten_39 (Flatten)            (None, 1536)         0           input_1[0][0]                    
__________________________________________________________________________________________________
flatten_40 (Flatten)            (None, 26)           0           input_2[0][0]                    
______________________________________________________________________________________

In [113]:
filepath="weights_bert_cnn.best_copy.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor='val_loss', verbose=0, save_best_only=True, mode='min')

history_model = model.fit([final_text_vector_train,train_vect_cat_num], 
                          y_train, 
                                 epochs=50,
                                 verbose=2,batch_size=64,
                                 callbacks = [checkpoint],
                                 validation_split = 0.05)

Epoch 1/50
77/77 - 0s - loss: 0.4278 - mae: 0.1716 - val_loss: 0.4115 - val_mae: 0.1640
Epoch 2/50
77/77 - 0s - loss: 0.4096 - mae: 0.1601 - val_loss: 0.4058 - val_mae: 0.1604
Epoch 3/50
77/77 - 0s - loss: 0.4059 - mae: 0.1571 - val_loss: 0.4035 - val_mae: 0.1587
Epoch 4/50
77/77 - 0s - loss: 0.4028 - mae: 0.1551 - val_loss: 0.4063 - val_mae: 0.1610
Epoch 5/50
77/77 - 0s - loss: 0.4028 - mae: 0.1546 - val_loss: 0.4012 - val_mae: 0.1547
Epoch 6/50
77/77 - 0s - loss: 0.4003 - mae: 0.1535 - val_loss: 0.3987 - val_mae: 0.1527
Epoch 7/50
77/77 - 0s - loss: 0.3999 - mae: 0.1526 - val_loss: 0.3977 - val_mae: 0.1535
Epoch 8/50
77/77 - 0s - loss: 0.3978 - mae: 0.1516 - val_loss: 0.3972 - val_mae: 0.1521
Epoch 9/50
77/77 - 0s - loss: 0.3974 - mae: 0.1512 - val_loss: 0.3975 - val_mae: 0.1555
Epoch 10/50
77/77 - 0s - loss: 0.3954 - mae: 0.1498 - val_loss: 0.3948 - val_mae: 0.1542
Epoch 11/50
77/77 - 0s - loss: 0.3946 - mae: 0.1496 - val_loss: 0.3931 - val_mae: 0.1494
Epoch 12/50
77/77 - 0s - loss:

In [114]:
model.load_weights("weights_bert_cnn.best_copy.hdf5")

# spearman's correlation on train data

y_tr_pred = model.predict([final_text_vector_train,train_vect_cat_num])
spearman(y_tr_pred,y_train)


0.32577724864112556

In [115]:
# spearman's correlation on CV data
y_cv_pred = model.predict([final_text_vector_cv, cv_vect_cat_num])
spearman(y_cv_pred,y_cv)

0.27272633128985574

## Model - CNN-3
This model performs CNN on ALBERT's text vector output and also on Categorical+Numerical data

In [117]:
#fixing numpy RS
np.random.seed(42)

#fixing tensorflow RS
tensorflow.random.set_seed(32)
    
#python RS
rn.seed(12)

#input 1
input1 = Input(shape=(1536,1), name = 'input_1')
conv = Conv1D(filters = 32, kernel_size = 11,strides = 2, activation='relu',
                  kernel_initializer=tensorflow.keras.initializers.he_normal(seed=43),
                  kernel_regularizer=tensorflow.keras.regularizers.l2(0.3),
                  input_shape=(None,1536,1))(input1)
conv = MaxPooling1D()(conv)
conv = Conv1D(32, 11, activation='relu',kernel_initializer=tensorflow.keras.initializers.he_normal(seed=43))(conv)
conv = MaxPooling1D()(conv)
flat_text = Flatten()(conv)
out_1 =  Dense(60,activation='sigmoid')(flat_text)
#====================================================================================================================

#input 2
input2 = Input(shape=(26,1), name = 'input_2')
conv = Conv1D(filters = 32, kernel_size = 3,strides = 2, activation='relu',
                  kernel_initializer=tensorflow.keras.initializers.he_normal(seed=43),
                  kernel_regularizer=tensorflow.keras.regularizers.l2(0.1),
                  input_shape=(None,26,1))(input2)

conv = MaxPooling1D()(conv)
conv = Conv1D(32, 3,  activation='relu',kernel_initializer=tensorflow.keras.initializers.he_normal(seed=43))(conv)
conv = MaxPooling1D()(conv)
flat_rem = Flatten()(conv)
out_2 =  Dense(30,activation='sigmoid')(flat_rem)
#====================================================================================================================

final_data = concatenate([out_1,out_2])

#====================================================================================================================

output = Dense(30,activation='sigmoid',kernel_initializer=tensorflow.keras.initializers.glorot_uniform(seed=45))(final_data)

    # create model with 2 inputs
model = Model([input1,input2], output)

model.compile(loss=tensorflow.keras.losses.binary_crossentropy,
              optimizer=tensorflow.keras.optimizers.Adam(0.001),
              metrics=['mae'])
model.summary()

Model: "functional_41"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            [(None, 1536, 1)]    0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            [(None, 26, 1)]      0                                            
__________________________________________________________________________________________________
conv1d_45 (Conv1D)              (None, 763, 32)      384         input_1[0][0]                    
__________________________________________________________________________________________________
conv1d_47 (Conv1D)              (None, 12, 32)       128         input_2[0][0]                    
______________________________________________________________________________________

In [118]:
filepath="weights_bert_cnn.best_copy.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor='val_loss', verbose=0, save_best_only=True, mode='min')

history_model = model.fit([final_text_vector_train,train_vect_cat_num], 
                          y_train, 
                                 epochs=50,
                                 verbose=2,batch_size=64,
                                 callbacks = [checkpoint],
                                 validation_split = 0.05)

Epoch 1/50
77/77 - 1s - loss: 23.8053 - mae: 0.2227 - val_loss: 20.9245 - val_mae: 0.1810
Epoch 2/50
77/77 - 1s - loss: 18.6519 - mae: 0.1754 - val_loss: 16.5004 - val_mae: 0.1744
Epoch 3/50
77/77 - 1s - loss: 14.7586 - mae: 0.1720 - val_loss: 13.1018 - val_mae: 0.1726
Epoch 4/50
77/77 - 1s - loss: 11.7523 - mae: 0.1712 - val_loss: 10.4640 - val_mae: 0.1726
Epoch 5/50
77/77 - 1s - loss: 9.4119 - mae: 0.1709 - val_loss: 8.4055 - val_mae: 0.1722
Epoch 6/50
77/77 - 1s - loss: 7.5798 - mae: 0.1701 - val_loss: 6.7888 - val_mae: 0.1707
Epoch 7/50
77/77 - 1s - loss: 6.1400 - mae: 0.1690 - val_loss: 5.5154 - val_mae: 0.1700
Epoch 8/50
77/77 - 1s - loss: 5.0002 - mae: 0.1659 - val_loss: 4.5028 - val_mae: 0.1636
Epoch 9/50
77/77 - 1s - loss: 4.0955 - mae: 0.1606 - val_loss: 3.7026 - val_mae: 0.1615
Epoch 10/50
77/77 - 1s - loss: 3.3798 - mae: 0.1577 - val_loss: 3.0675 - val_mae: 0.1591
Epoch 11/50
77/77 - 1s - loss: 2.8110 - mae: 0.1554 - val_loss: 2.5640 - val_mae: 0.1561
Epoch 12/50
77/77 - 1s

In [119]:
model.load_weights("weights_bert_cnn.best_copy.hdf5")

In [120]:
y_tr_pred = model.predict([final_text_vector_train,train_vect_cat_num])
spearman(y_tr_pred,y_train)

0.310878976892461

In [121]:
y_cv_pred = model.predict([final_text_vector_cv, cv_vect_cat_num])
spearman(y_cv_pred,y_cv)

0.2717920296879318

## Model-4

This model simply passed the ALBERT's text vector to a Dense layer with 1024 activation units and finally to th output layer

In [131]:
# input layer
input1 = Input(shape=(1536,), name = 'input_1')

# DENSE layer
x = Dense(1024, activation='relu')(input1)

# final output
output = Dense(30,activation='sigmoid',kernel_initializer=tensorflow.keras.initializers.glorot_uniform())(x)

# create model
model = Model(input1, output)

model.compile(loss=tensorflow.keras.losses.binary_crossentropy,
              optimizer=tensorflow.keras.optimizers.Adam(0.001),
              metrics=['mae'])
              
model.summary()

Model: "functional_49"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         [(None, 1536)]            0         
_________________________________________________________________
dense_71 (Dense)             (None, 1024)              1573888   
_________________________________________________________________
dense_72 (Dense)             (None, 30)                30750     
Total params: 1,604,638
Trainable params: 1,604,638
Non-trainable params: 0
_________________________________________________________________


In [132]:
# fitting on train data
filepath="weights_bert_cnn.best_copy.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor='val_loss', verbose=0, save_best_only=True, mode='min')

history_model = model.fit(final_text_vector_train, 
                          y_train, 
                                 epochs=60,
                                 verbose=2,batch_size=128,
                                 callbacks = [checkpoint],
                                 validation_split = 0.1)


Epoch 1/60
37/37 - 0s - loss: 0.4535 - mae: 0.1735 - val_loss: 0.4073 - val_mae: 0.1609
Epoch 2/60
37/37 - 0s - loss: 0.4082 - mae: 0.1576 - val_loss: 0.4020 - val_mae: 0.1562
Epoch 3/60
37/37 - 0s - loss: 0.4045 - mae: 0.1553 - val_loss: 0.4050 - val_mae: 0.1618
Epoch 4/60
37/37 - 0s - loss: 0.4035 - mae: 0.1551 - val_loss: 0.3992 - val_mae: 0.1585
Epoch 5/60
37/37 - 0s - loss: 0.3996 - mae: 0.1529 - val_loss: 0.3963 - val_mae: 0.1568
Epoch 6/60
37/37 - 0s - loss: 0.3983 - mae: 0.1520 - val_loss: 0.3992 - val_mae: 0.1544
Epoch 7/60
37/37 - 0s - loss: 0.3982 - mae: 0.1513 - val_loss: 0.3952 - val_mae: 0.1520
Epoch 8/60
37/37 - 0s - loss: 0.3956 - mae: 0.1497 - val_loss: 0.3935 - val_mae: 0.1528
Epoch 9/60
37/37 - 0s - loss: 0.3929 - mae: 0.1483 - val_loss: 0.3929 - val_mae: 0.1525
Epoch 10/60
37/37 - 0s - loss: 0.3925 - mae: 0.1479 - val_loss: 0.3925 - val_mae: 0.1525
Epoch 11/60
37/37 - 0s - loss: 0.3919 - mae: 0.1477 - val_loss: 0.3929 - val_mae: 0.1530
Epoch 12/60
37/37 - 0s - loss:

In [133]:
# loading best weights
model.load_weights("weights_bert_cnn.best_copy.hdf5")

# spearman's correlation on train data
y_tr_pred = model.predict([final_text_vector_train,train_vect_cat_num])
print("Train score = ",spearman(y_tr_pred,y_train))

# spearman's correlation on CV data
y_cv_pred = model.predict([final_text_vector_cv, cv_vect_cat_num])
print("Validation score",spearman(y_cv_pred,y_cv))

Train score =  0.33316380247527433
Validation score 0.27269591176848407


### Model- 5

This model performs convolution separately on Question and Answer vector output of ALBERT

In [137]:

 #fixing numpy RS
np.random.seed(42)

 #fixing tensorflow RS
tensorflow.random.set_seed(32)
    
 #python RS
rn.seed(12)

#input 0
input0 = Input(shape=(768,1), name = 'input_0')
conv = Conv1D(filters = 16, kernel_size = 7,strides = 2, activation='relu',
                  kernel_initializer=tensorflow.keras.initializers.he_normal(seed=43),
                  kernel_regularizer=tensorflow.keras.regularizers.l2(0.2),
                  input_shape=(None,768,1))(input0)

flat_text0 = Flatten()(conv)
out_0 =  Dense(256,activation='sigmoid')(flat_text0)
#===================================================================================================================
    #input 1
input1 = Input(shape=(768,1), name = 'input_1')
conv = Conv1D(filters = 16, kernel_size = 7,strides = 2, activation='relu',
                  kernel_initializer=tensorflow.keras.initializers.he_normal(seed=43),
                  kernel_regularizer=tensorflow.keras.regularizers.l2(0.2),
                  input_shape=(None,768,1))(input1)

flat_text = Flatten()(conv)
out_1 =  Dense(256,activation='sigmoid')(flat_text)
#====================================================================================================================

#input 2
input2 = Input(shape=(26,1), name = 'input_2')
conv = Conv1D(filters = 8, kernel_size = 3,strides = 2, activation='relu',
                  kernel_initializer=tensorflow.keras.initializers.he_normal(seed=43),
                  kernel_regularizer=tensorflow.keras.regularizers.l2(0.1),
                  input_shape=(None,26,1))(input2)


flat_rem = Flatten()(conv)
out_2 =  Dense(24,activation='sigmoid')(flat_rem)

#====================================================================================================================

final_data = concatenate([out_0,out_1,out_2])

#====================================================================================================================
# output
output = Dense(30,activation='sigmoid',kernel_initializer=tensorflow.keras.initializers.glorot_uniform(seed=45))(final_data)

# create model with 3 inputs
model = Model([input0,input1,input2], output)

model.compile(loss=tensorflow.keras.losses.binary_crossentropy,
              optimizer=tensorflow.keras.optimizers.Adam(0.002),
              metrics=['mae'])
model.summary()

Model: "functional_53"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_0 (InputLayer)            [(None, 768, 1)]     0                                            
__________________________________________________________________________________________________
input_1 (InputLayer)            [(None, 768, 1)]     0                                            
__________________________________________________________________________________________________
input_2 (InputLayer)            [(None, 26, 1)]      0                                            
__________________________________________________________________________________________________
conv1d_52 (Conv1D)              (None, 381, 16)      128         input_0[0][0]                    
______________________________________________________________________________________

In [138]:
filepath="weights_bert_cnn.best_copy.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor='val_loss', verbose=0, save_best_only=True, mode='min')

history_model = model.fit([question_vect,answer_vect,train_vect_cat_num], 
                          y_train, 
                                 epochs=70,
                                 verbose=2,batch_size=128,
                                 callbacks = [checkpoint],
                                 validation_split = 0.1)

Epoch 1/70
37/37 - 1s - loss: 14.0034 - mae: 0.1814 - val_loss: 12.5602 - val_mae: 0.1717
Epoch 2/70
37/37 - 0s - loss: 11.4436 - mae: 0.1686 - val_loss: 10.3029 - val_mae: 0.1692
Epoch 3/70
37/37 - 0s - loss: 9.4063 - mae: 0.1653 - val_loss: 8.4865 - val_mae: 0.1676
Epoch 4/70
37/37 - 0s - loss: 7.7617 - mae: 0.1629 - val_loss: 7.0140 - val_mae: 0.1636
Epoch 5/70
37/37 - 0s - loss: 6.4250 - mae: 0.1609 - val_loss: 5.8148 - val_mae: 0.1630
Epoch 6/70
37/37 - 0s - loss: 5.3341 - mae: 0.1594 - val_loss: 4.8355 - val_mae: 0.1609
Epoch 7/70
37/37 - 0s - loss: 4.4416 - mae: 0.1584 - val_loss: 4.0316 - val_mae: 0.1595
Epoch 8/70
37/37 - 0s - loss: 3.7092 - mae: 0.1576 - val_loss: 3.3719 - val_mae: 0.1597
Epoch 9/70
37/37 - 0s - loss: 3.1066 - mae: 0.1565 - val_loss: 2.8281 - val_mae: 0.1582
Epoch 10/70
37/37 - 0s - loss: 2.6115 - mae: 0.1560 - val_loss: 2.3813 - val_mae: 0.1579
Epoch 11/70
37/37 - 0s - loss: 2.2031 - mae: 0.1552 - val_loss: 2.0125 - val_mae: 0.1565
Epoch 12/70
37/37 - 0s - l

In [139]:
model.load_weights("weights_bert_cnn.best_copy.hdf5")

y_tr_pred = model.predict([question_vect,answer_vect,train_vect_cat_num])
print(spearman(y_tr_pred,y_train))

y_cv_pred = model.predict([question_vect_cv,answer_vect_cv,cv_vect_cat_num])
print(spearman(y_cv_pred,y_cv))

0.2990366448517647
0.2714259127874635


### Among all the 5 models, overall good performing and minimum overfit model is Model-5  - Train score = 0.299 and Validation score = 0.271.